In [10]:
# https://www.tensorflow.org/tutorials/layers
# Импорт библиотек
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Импорт библиотеки для работы с массивами и тензорфлоу
import numpy as np
import tensorflow as tf

# Настройка выводимой в логах информации, аналог vebrose
tf.logging.set_verbosity(tf.logging.INFO)

def cnn_model_fn(features, labels, mode): # Построение нейронной сети
    
  # Входной слой, размер уменьшен до 32х32, как у CIFAR-10
  input_layer = tf.reshape(features["x"], [-1, 32, 32, 1])

  # Сверточный слой 1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[3, 3],
      padding="same",
      activation=tf.nn.relu)

  # Слой пулинга 1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Сверточный слой 2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[3, 3],
      padding="same",
      activation=tf.nn.relu)
  
  # Слой пулинга 2
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Сверточный слой 3
  conv3 = tf.layers.conv2d(
      inputs=pool2,
      filters=128,
      kernel_size=[3, 3],
      padding="same",
      activation=tf.nn.relu)
  
  # Слой пулинга 3
  pool3 = tf.layers.max_pooling2d(inputs=conv3, pool_size=[2, 2], strides=2)
 
  # Разверточный слой 1
  deconv1 = tf.layers.deconv2d(
      inputs=pool3,
      filters=64,
      kernel_size=[3, 3],
      padding="same",
      activation=tf.nn.relu)
  
  # Слой анпулинга 1
  pre_unpool1 = tf.layers.max_pooling2d(inputs=deconv1, pool_size=[2, 2], strides=2)
  unpool1 = unpool(pre_unpool1, ind, kernel_size=(1, 2, 2, 1), scope='unpool')
    
  # Разверточный слой 2
  deconv2 = tf.layers.deconv2d(
      inputs=unpool1,
      filters=32,
      kernel_size=[3, 3],
      padding="same",
      activation=tf.nn.relu)
  
  # Слой пулинга 3
  pre_unpool2 = tf.layers.max_pooling2d(inputs=deconv2, pool_size=[2, 2], strides=2)
  unpool2 = unpool(pre_unpool2, ind, kernel_size=(1, 2, 2, 1), scope='unpool')
 

  # Изменение размерности входящего слоя, аналог Flatten()
  unpool2_flat = tf.reshape(unpool2, [-1, 7 * 7 * 64])
    
  # Полносвязный слой и дропаут
  dense = tf.layers.dense(inputs=unpool2_flat, units=128, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Слой-классификатор с 10 нейронами для 10 классов
  logits = tf.layers.dense(inputs=dropout, units=10)

  # Формирование результатов
  predictions = {
      # Определение класса для каждого объекта
      "classes": tf.argmax(input=logits, axis=1),
      # 
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Для обеих моделей подсчитваем потери методом категориальной кросс энтропии
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Настройка оптимизатора для модели, стохастический градиентный спуск
  if mode == tf.estimator.ModeKeys.TRAIN: # Если набор данных - тренировочный
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001) # Тренируем сеть с использованием SGD
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Добавление метрики 
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

# Слой анпулинга, взято из https://github.com/tensorflow/tensorflow/issues/2169#issuecomment-216607417
def unpool(pool, ind, ksize=(1, 2, 2, 1), scope='unpool'):
    """
       Unpooling layer after max_pool_with_argmax.
       Args:
           pool:   max pooled output tensor
           ind:      argmax indices (produced by tf.nn.max_pool_with_argmax)
           ksize:     ksize is the same as for the pool
       Return:
           unpooled:    unpooling tensor
    """
    with tf.variable_scope(scope):
        pooled_shape = pool.get_shape().as_list()

        flatten_ind = tf.reshape(ind, (pooled_shape[0], pooled_shape[1] * pooled_shape[2] * pooled_shape[3]))
        # sparse indices to dense ones_like matrics
        one_hot_ind = tf.one_hot(flatten_ind,  pooled_shape[1] * ksize[1] * pooled_shape[2] * ksize[2] * pooled_shape[3], on_value=1., off_value=0., axis=-1)
        one_hot_ind = tf.reduce_sum(one_hot_ind, axis=1)
        one_like_mask = tf.reshape(one_hot_ind, (pooled_shape[0], pooled_shape[1] * ksize[1], pooled_shape[2] * ksize[2], pooled_shape[3]))
        # resize input array to the output size by nearest neighbor
        img = tf.image.resize_nearest_neighbor(pool, [pooled_shape[1] * ksize[1], pooled_shape[2] * ksize[2]])
        unpooled = tf.multiply(img, tf.cast(one_like_mask, img.dtype))
        return unpooled

def main():
  # Загружаем данные для обучения и оценки
  dataset = tf.contrib.learn.datasets.load_dataset("D://KT_dataset/cifarpascal")
  train_data = dataset.train.images # массив numpy для данных обучения
  train_labels = np.asarray(dataset.train.labels, dtype=np.int32) # Приводим к целочисленным значениям
  eval_data = dataset.test.images # массив numpy для данных оценки
  eval_labels = np.asarray(dataset.test.labels, dtype=np.int32) # Приводим к целочисленным значениям
    
  # Добавляем Estimator - класс в TensorFlow для высокоуровнего обучения и оценки моделей
  classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/testmodel/") 

  # Периодическое занесение данных в лог
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

  # Общие настройки данных для обучения
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=35,
    shuffle=True)
  classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

  # Общие настройки данных для обучения
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
  print(eval_results)

    
if __name__ == '__main__':
  tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/testmodel/', '_tf_random_seed': 1, '_save_summary_steps': 100, '_save_checkpoints_secs': 600, '_save_checkpoints_steps': None, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /testmodel/model.ckpt.
INFO:tensorflow:loss = 2.3188, step = 1
INFO:tensorflow:probabilities = [[ 0.09423882  0.11018304  0.08645301  0.10867312  0.10390012  0.08781934
   0.09109475  0.09743519  0.10257386  0.11762863]
 [ 0.08881238  0.11528443  0.07277734  0.11603725  0.11792506  0.08852896
   0.10917858  0.08932498  0.09439886  0.10773212]
 [ 0.09185039  0.10906845  0.08970839  0.11109397  0.10306378  0.0

INFO:tensorflow:probabilities = [[ 0.09028256  0.10947178  0.07502775  0.11161095  0.09557799  0.09184041
   0.10649369  0.10327052  0.10380533  0.112619  ]
 [ 0.07147602  0.11349925  0.08407158  0.10186238  0.10525916  0.10003443
   0.09812748  0.0941109   0.11301784  0.11854095]
 [ 0.09296025  0.11248313  0.09013047  0.1035173   0.09629384  0.09037989
   0.10392417  0.09107164  0.09609514  0.12314408]
 [ 0.10099931  0.10520136  0.10149888  0.11050815  0.10069473  0.08293401
   0.10377224  0.08286604  0.09838037  0.11314492]
 [ 0.10058604  0.10368181  0.09410442  0.10948529  0.10475337  0.09059005
   0.1084548   0.08524626  0.09233823  0.11075976]
 [ 0.09009726  0.10615307  0.08515555  0.10348519  0.11102824  0.09043051
   0.10284077  0.1100165   0.0897866   0.1110063 ]
 [ 0.09655043  0.1190052   0.09200041  0.10578789  0.09282489  0.08832751
   0.11452863  0.10045711  0.09062625  0.09989174]
 [ 0.09619474  0.10350646  0.0869678   0.1064648   0.10357883  0.09422885
   0.11228466  0.09

INFO:tensorflow:global_step/sec: 5.16446
INFO:tensorflow:loss = 2.28179, step = 101 (19.364 sec)
INFO:tensorflow:probabilities = [[ 0.10365234  0.10710251  0.09316973  0.10547874  0.09348319  0.09852971
   0.10624579  0.09745279  0.08977685  0.10510831]
 [ 0.10309961  0.10463843  0.08347505  0.10545072  0.1020649   0.08291133
   0.10716583  0.10934866  0.08764467  0.11420085]
 [ 0.1069757   0.09252895  0.09147484  0.10201209  0.10092738  0.10444366
   0.09659951  0.09335942  0.09795952  0.11371902]
 [ 0.09190304  0.11568408  0.0912611   0.10706481  0.09629734  0.09121131
   0.11086093  0.08959705  0.10046408  0.10565621]
 [ 0.10775751  0.11058845  0.08556566  0.10945823  0.10260351  0.0958813
   0.09398526  0.10344142  0.08161614  0.1091025 ]
 [ 0.09495713  0.11285321  0.09473104  0.11889048  0.10428335  0.08424282
   0.10079476  0.0883444   0.08865174  0.11225104]
 [ 0.08684663  0.10722462  0.09435103  0.10285731  0.10475763  0.09811857
   0.10609243  0.08596203  0.10472152  0.1090682

INFO:tensorflow:probabilities = [[ 0.0971585   0.09536079  0.09628329  0.10440034  0.09880669  0.09674921
   0.10819697  0.08273029  0.11173202  0.10858186]
 [ 0.08659793  0.10509407  0.0884411   0.11308865  0.09907401  0.09126306
   0.10584205  0.10210694  0.09614601  0.11234615]
 [ 0.0963797   0.1060679   0.0951233   0.09179215  0.10664494  0.0978218
   0.0954887   0.08777524  0.11215048  0.11075573]
 [ 0.08998796  0.10271841  0.08952068  0.12707856  0.09608251  0.08545013
   0.10012232  0.08488717  0.1034577   0.12069448]
 [ 0.08940392  0.09696707  0.08829346  0.11176588  0.09858796  0.09302093
   0.11908851  0.09330659  0.10217914  0.10738659]
 [ 0.09666143  0.10512815  0.09024186  0.10461211  0.09559708  0.09046847
   0.09432834  0.10046106  0.10951336  0.11298808]
 [ 0.08236536  0.09626235  0.08803479  0.11647296  0.10417805  0.09551879
   0.11178813  0.09399419  0.1111379   0.10024744]
 [ 0.08784999  0.11314077  0.08520341  0.11654986  0.09584665  0.09302212
   0.10026706  0.106

INFO:tensorflow:global_step/sec: 5.28455
INFO:tensorflow:loss = 2.24994, step = 201 (18.924 sec)
INFO:tensorflow:probabilities = [[ 0.09736466  0.09981465  0.09446119  0.11700761  0.10617613  0.09179441
   0.09410445  0.09934934  0.09429933  0.10562815]
 [ 0.09389     0.10298583  0.08266579  0.09655934  0.10970934  0.09895176
   0.10400711  0.10531896  0.08994709  0.1159648 ]
 [ 0.1074084   0.096444    0.09242748  0.11037317  0.09542763  0.09936608
   0.10822798  0.09012054  0.09710397  0.10310074]
 [ 0.09875024  0.09432609  0.093424    0.10702915  0.10449278  0.09883123
   0.10538401  0.08872212  0.10880241  0.10023797]
 [ 0.08799101  0.10803704  0.08340888  0.1180836   0.09882259  0.10148492
   0.11075573  0.08611598  0.09860664  0.10669367]
 [ 0.09531564  0.10662992  0.09737197  0.10167529  0.09607986  0.08189508
   0.1049999   0.09624818  0.10194657  0.11783759]
 [ 0.09483214  0.10185491  0.09133729  0.11487976  0.08518137  0.09445262
   0.09431833  0.10737099  0.10507996  0.110692

...

INFO:tensorflow:global_step/sec: 5.10357
INFO:tensorflow:loss = 0.16699, step = 19801 (19.591 sec)
INFO:tensorflow:probabilities = [[ 0.0000554   0.98013407  0.00076347  0.00252007  0.00032495  0.00008991
   0.00006605  0.01207392  0.00132187  0.00265045]
 [ 0.00001265  0.99491078  0.00028496  0.00105162  0.00014963  0.00057195
   0.00037566  0.0011313   0.00082857  0.00068282]
 [ 0.          0.00000041  0.00000153  0.99993169  0.          0.00000565
   0.          0.00000899  0.0000009   0.0000509 ]
 [ 0.00733988  0.00011432  0.00120587  0.92811811  0.00012666  0.05533101
   0.00018088  0.00013674  0.0046687   0.0027778 ]
 [ 0.00505217  0.00055421  0.00931415  0.00061157  0.91547966  0.00378136
   0.02895529  0.00012625  0.02655191  0.00957344]
 [ 0.00000003  0.          0.00000007  0.00000004  0.99997675  0.00001411
   0.00000382  0.00000052  0.00000012  0.0000047 ]
 [ 0.00016039  0.00007148  0.31481114  0.64587325  0.00000025  0.00084073
   0.00000021  0.00000726  0.03806138  0.0001

INFO:tensorflow:probabilities = [[ 0.00002177  0.00008663  0.00015619  0.00301148  0.0000001   0.00000059
   0.00000001  0.98971015  0.0008239   0.00618929]
 [ 0.00036893  0.98358971  0.00108055  0.00040812  0.00022609  0.00011654
   0.00249443  0.00012161  0.01152598  0.00006797]
 [ 0.          0.          0.00000001  0.00001011  0.          0.00000003
   0.          0.99998844  0.00000003  0.00000147]
 [ 0.00183752  0.00024494  0.00043644  0.00737111  0.06649659  0.01160008
   0.00005048  0.14104007  0.00233097  0.76859176]
 [ 0.00000041  0.0000013   0.00003403  0.00009305  0.00278969  0.00000036
   0.00000001  0.00437729  0.0000484   0.99265552]
 [ 0.00000218  0.00001619  0.00003686  0.00004688  0.97251046  0.00000909
   0.00002102  0.00136725  0.00069539  0.02529463]
 [ 0.00031527  0.00000006  0.983567    0.01605923  0.00000317  0.00000225
   0.00000009  0.00000031  0.0000511   0.0000015 ]
 [ 0.00007301  0.00023185  0.00008358  0.000303    0.00003183  0.00283379
   0.00008773  0.00

INFO:tensorflow:global_step/sec: 5.19748
INFO:tensorflow:loss = 0.168983, step = 19901 (19.241 sec)
INFO:tensorflow:probabilities = [[ 0.00000852  0.00000466  0.00005099  0.00005516  0.00568792  0.00001438
   0.00000105  0.00031457  0.00026437  0.99359834]
 [ 0.0000043   0.00000083  0.00045653  0.00027327  0.00110074  0.00000246
   0.00000001  0.00038987  0.000495    0.99727696]
 [ 0.0000231   0.00028798  0.00190323  0.00024582  0.00031046  0.00004575
   0.99697971  0.00000002  0.00020384  0.00000006]
 [ 0.046397    0.00008186  0.17033955  0.00182714  0.00000348  0.00012758
   0.00002365  0.73067707  0.00070295  0.0498197 ]
 [ 0.00006928  0.00457803  0.00353161  0.00082182  0.96788341  0.00407588
   0.01296569  0.00030091  0.00347646  0.00229704]
 [ 0.00049883  0.97214681  0.00829486  0.00369042  0.00090823  0.00025542
   0.00210675  0.00495005  0.00662416  0.00052452]
 [ 0.00003176  0.99350101  0.00039452  0.00041327  0.00033921  0.00006392
   0.00008079  0.00393879  0.0005989   0.000

INFO:tensorflow:probabilities = [[ 0.00000407  0.00000899  0.00001824  0.88430637  0.00000042  0.1126454
   0.00001391  0.00000001  0.00299928  0.00000342]
 [ 0.00000009  0.0000302   0.00001626  0.00030841  0.00000807  0.00000035
   0.          0.99904817  0.00001635  0.00057215]
 [ 0.0000147   0.00000022  0.00019792  0.0005579   0.00000917  0.00001326
   0.00000029  0.00000091  0.99889416  0.00031155]
 [ 0.00000007  0.00000012  0.00000008  0.99979955  0.00000012  0.00011581
   0.          0.00000086  0.00001898  0.00006453]
 [ 0.          0.00000001  0.0000001   0.00003598  0.          0.00000012
   0.          0.99980992  0.00000017  0.00015375]
 [ 0.95750242  0.00001586  0.00020685  0.00268223  0.00000147  0.03460641
   0.00038776  0.00362956  0.00028291  0.00068447]
 [ 0.00007592  0.00023211  0.0006388   0.00397829  0.00423827  0.00275779
   0.00439197  0.00000897  0.98363322  0.00004463]
 [ 0.00008629  0.00000544  0.0002307   0.00000042  0.00037674  0.00080757
   0.99847573  0.000

INFO:tensorflow:Saving checkpoints for 20000 into /testmodel/model.ckpt.
INFO:tensorflow:Loss for final step: 0.103578.
INFO:tensorflow:Starting evaluation at 2018-03-03-21:46:39
INFO:tensorflow:Restoring parameters from /testmodel/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-03-21:46:45
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9689, global_step = 20000, loss = 0.104999
{'accuracy': 0.96890002, 'loss': 0.10499919, 'global_step': 20000}
